In [1]:
!pip install datasets==2.5.0 # https://github.com/huggingface/datasets/issues/5111
!pip install matplotlib==3.5.3 # Need >=3.5.0 https://stackoverflow.com/questions/21910986/why-set-xticks-doesnt-set-the-labels-of-ticks
!GIT_LFS_SKIP_SMUDGE=1 git clone https://huggingface.co/datasets/bigscience/evaluation-results

# RESTART RUNTIME #

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 431.2/431.2 KB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 KB 19.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.2/199.2 KB 24.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 95.8/95.8 KB 12.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 KB 24.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 14.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 KB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 KB 14.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 KB 26.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.3/132.3 KB 11.3 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/si

Cloning into 'evaluation-results'...
remote: Enumerating objects: 90408, done.
remote: Counting objects: 100% (302/302), done.
remote: Compressing objects: 100% (47/47), done.
remote: Total 90408 (delta 125), reused 299 (delta 122), pack-reused 90106
Receiving objects: 100% (90408/90408), 38.57 MiB | 19.45 MiB/s, done.
Resolving deltas: 100% (42060/42060), done.
Updating files: 100% (47486/47486), done.


In [25]:
for model in ["bloomz", "bloomz-560m", "bloomz-1b1", "bloomz-1b7", "bloomz-3b", "bloomz-7b1", "mt0-small", "mt0-base", "mt0-large", "mt0-xl", "mt0-xxl"]:
  !mkdir -p evaluation-results/{model}/bigsciencelmevalharness/transformers
  !cp -r evaluation-results/{model}/bloomzeval/transformers/evaluation_val/*wmt* evaluation-results/{model}/bigsciencelmevalharness/transformers/
  !cp -r evaluation-results/{model}/bloomzeval/transformers/evaluation_val/*mlsum* evaluation-results/{model}/bigsciencelmevalharness/transformers/

def get_paths(base_dir="bloom"):
    import json, glob, os
    str_to_replace = ["?", " ", "…", "=", ":"]
    files = {}
    for framework_dir in os.listdir(base_dir):
        conf_framework = os.path.join(base_dir, framework_dir)
        if not(os.path.isdir(conf_framework)):
            print("Skipping ", conf_framework)
            continue
        for ckpt_dir in os.listdir(conf_framework):
            conf_framework_ckpt = os.path.join(conf_framework, ckpt_dir)
            framework_ckpt = os.path.join(framework_dir, ckpt_dir)
            if not(os.path.isdir(conf_framework_ckpt)):
                print("Skipping ", conf_framework_ckpt)
                continue
            res_files = glob.glob(conf_framework_ckpt + '/**/*.*', recursive=True)
            for res_file in res_files:
                if res_file.endswith(".json"):
                    #print("GOT", res_file)
                    if "bigsciencelmevalharness" in framework_ckpt and "agg" in res_file:
                        continue # agg result files are not parsed
                    elif "bloomzeval" in framework_ckpt and "nospace" in res_file:
                        continue # Old results using no space between input & target
                    elif "bloomzeval" in framework_ckpt and "xwinograd_zh_short" in res_file:
                        continue # Old xwinograd dataset with few chinese samples
                    elif res_file.endswith(("generations.json", "references.json")):
                        continue 
                    clean_res_file = res_file
                    if any([x in res_file for x in str_to_replace]):
                        for x in str_to_replace:
                            clean_res_file = clean_res_file.replace(x, "")
                        os.renames(res_file, clean_res_file) # Rename incl parent dirs
                    files.setdefault(framework_ckpt, [])
                    files[framework_ckpt].append(clean_res_file)
    with open(f"{base_dir}paths.json", "w") as f:
        json.dump(files, f)
    return files

%cd evaluation-results
for model in ["bloomz", "bloomz-560m", "bloomz-1b1", "bloomz-1b7", "bloomz-3b", "bloomz-7b1", "mt0-small", "mt0-base", "mt0-large", "mt0-xl", "mt0-xxl"]:
  get_paths(model)
%cd ..

cp: cannot stat 'evaluation-results/bloomz-1b7/bloomzeval/transformers/evaluation_val/*mlsum*': No such file or directory
/content/evaluation-results
/content


In [ ]:
### Change paths to point to local onces ###

In [26]:
%%writefile evaluation-results/evaluation-results.py
# coding=utf-8
# Lint as: python3
"""BigScience evaluation results"""

import json

import datasets

logger = datasets.logging.get_logger(__name__)


_CITATION = """@article{scao2022bloom,
  title={BLOOM: A 176B-Parameter Open-Access Multilingual Language Model},
  author={Scao, Teven Le and Fan, Angela and Akiki, Christopher and Pavlick, Ellie and Ili{\'c}, Suzana and Hesslow, Daniel and Castagn{\'e}, Roman and Luccioni, Alexandra Sasha and Yvon, Fran{\c{c}}ois and Gall{\'e}, Matthias and others},
  journal={arXiv preprint arXiv:2211.05100},
  year={2022}
}"""

_DESCRIPTION = """
"""

import json

URLS = {
    "bloom": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloompaths.json",
    "bloom-7b1": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloom-7b1paths.json",
    "bloom-3b": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloom-3bpaths.json",
    "bloom-1b7": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloom-1b7paths.json",
    "bloom-1b1": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloom-1b1paths.json",
    "bloom-560m": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloom-560mpaths.json",
    "opt-350m": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/opt-350mpaths.json",
    "opt-1b3": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/opt-1b3paths.json",
    "opt-2b7": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/opt-2b7paths.json",
    "opt-6b7": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/opt-6b7paths.json",
    "opt175b": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/opt175bpaths.json",
    "t0": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/t0paths.json",
    "mt5-xxl": "mt5-xxlpaths.json",
    "mt0-small": "mt0-smallpaths.json",
    "mt0-base": "mt0-basepaths.json",
    "mt0-large": "mt0-largepaths.json",
    "mt0-xl": "mt0-xlpaths.json",
    "mt0-xxl": "mt0-xxlpaths.json",
    "mt0-xxl-p3": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/mt0-xxl-p3paths.json",
    "mt0-xxl-mt": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/mt0-xxl-mtpaths.json",
    "gpt-j": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/gpt-jpaths.json",
    "t5-xxl-lm-adapt": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/t5-xxl-lm-adaptpaths.json",
    "gpt2": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/gpt2paths.json",
    "mgpt": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/mgptpaths.json",
    "bloomz": "bloomzpaths.json",
    "bloomz-7b1": "bloomz-7b1paths.json",
    "bloomz-3b": "bloomz-3bpaths.json",
    "bloomz-1b7": "bloomz-1b7paths.json",
    "bloomz-1b1": "bloomz-1b1paths.json",
    "bloomz-560m": "bloomz-560mpaths.json",
    "bloomz-mt": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-mtpaths.json",
    "bloomz-7b1-mt": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-mtpaths.json",
    "bloomz-p3": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-p3paths.json",    
    "bloomz-7b1-p3": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-p3paths.json",        
    "xglm-7b5": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/xglm-7b5paths.json",        
    "mtk-instruct-3b-def-pos": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/mtk-instruct-3b-def-pospaths.json",
    "mtk-instruct-11b-def-pos": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/mtk-instruct-11b-def-pospaths.json",    
    "openai-davinci": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/openai-davincipaths.json",
    "bloomz-7b1-500m-ru": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-500m-rupaths.json",
    "bloomz-7b1-4b-ru": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-4b-rupaths.json",
    "bloomz-7b1-4b-xp3ru": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-4b-xp3rupaths.json",
    "bloomz-7b1-c4tasky": "https://huggingface.co/datasets/bigscience/evaluation-results/resolve/main/bloomz-7b1-c4taskypaths.json"
}

# To remove empty files: find ./ -size 0 -print -delete
def get_paths(base_dir="bloom"):
    import json, glob, os
    str_to_replace = ["?", " ", "…", "=", ":"]
    files = {}
    for framework_dir in os.listdir(base_dir):
        conf_framework = os.path.join(base_dir, framework_dir)
        if not(os.path.isdir(conf_framework)):
            print("Skipping ", conf_framework)
            continue
        for ckpt_dir in os.listdir(conf_framework):
            conf_framework_ckpt = os.path.join(conf_framework, ckpt_dir)
            framework_ckpt = os.path.join(framework_dir, ckpt_dir)
            if not(os.path.isdir(conf_framework_ckpt)):
                print("Skipping ", conf_framework_ckpt)
                continue
            res_files = glob.glob(conf_framework_ckpt + '/**/*.*', recursive=True)
            for res_file in res_files:
                if res_file.endswith(".json"):
                    if "bigsciencelmevalharness" in framework_ckpt and "agg" in res_file:
                        continue # agg result files are not parsed
                    elif "bloomzeval" in framework_ckpt and "nospace" in res_file:
                        continue # Old results using no space between input & target
                    elif "bloomzeval" in framework_ckpt and "xwinograd_zh_short" in res_file:
                        continue # Old xwinograd dataset with few chinese samples
                    elif res_file.endswith(("generations.json", "references.json")):
                        continue 
                    clean_res_file = res_file
                    if any([x in res_file for x in str_to_replace]):
                        for x in str_to_replace:
                            clean_res_file = clean_res_file.replace(x, "")
                        os.renames(res_file, clean_res_file) # Rename incl parent dirs
                    files.setdefault(framework_ckpt, [])
                    files[framework_ckpt].append(clean_res_file)
    with open(f"{base_dir}paths.json", "w") as f:
        json.dump(files, f)
    return files


class BLOOMEval(datasets.GeneratorBasedBuilder):
    """"""

    VERSION = datasets.Version("1.0.0")
    BUILDER_CONFIGS = [
        datasets.BuilderConfig(
            name=k,
            version=datasets.Version("1.0.0"),
            description=k,
        ) for k in URLS.keys()
    ]
    DEFAULT_CONFIG_NAME = "bloom176b"

    def _info(self):
        return datasets.DatasetInfo(
            description=_DESCRIPTION,
            features=datasets.Features(
                {
                    "evaluation_framework": datasets.Value("string"),
                    "checkpoint_type": datasets.Value("string"),
                    "task_name": datasets.Value("string"),
                    "prompt_name": datasets.Value("string"),
                    "metric": datasets.Value("string"),
                    "score": datasets.Value("float32"),
                    "fewshots": datasets.Value("int8"),
                }
            ),
            supervised_keys=None,
            citation=_CITATION,
        )

    def _split_generators(self, dl_manager):

        path_file = dl_manager.download_and_extract(URLS[self.config.name])
        with open(path_file, "r") as f:
            files = json.load(f)

        downloaded_files = dl_manager.download_and_extract(files)
        return [
            datasets.SplitGenerator(
                name=datasets.Split.TEST,
                gen_kwargs={'filepath': downloaded_files}
            )
        ]

    def _generate_examples(self, filepath):
        """This function returns the examples in the raw (text) form."""
        logger.info("Generating examples from", filepath)
        
        out = []

        for k, paths in filepath.items():
            if k == "bigsciencelmevalharness/megatrondeepspeed":
                out.extend(parse_bslmeval_megds(paths))
            elif k == "bigsciencelmevalharness/transformers":
                out.extend(parse_bslmeval_transformers(paths))
            elif k == "lmevalharness/megatrondeepspeed":
                out.extend(parse_lmeval_megds(paths))
            elif k == "codeeval/transformers":
                out.extend(parse_codeeval(paths))
            elif k == "bloomzeval/transformers":
                out.extend(parse_bloomzeval(paths))

        for idx, row in enumerate(out):
            yield idx, row

def parse_bslmeval_megds(paths):
    out = []
    for p in paths:
        res = json.load(open(p, "r"))
        for ex in res.get("results", []):
            if not isinstance(ex, dict):
                continue
            out.append({
                "evaluation_framework": "bigscience/lm-evaluation-harness",
                "checkpoint_type": "megatrondeepspeed",
                "task_name": ex.get("task_name", None),
                "prompt_name": ex.get("prompt_name", None),
                "metric": [x for x in ex if (isinstance(ex[x], float) and "stderr" not in x)][0],
                "score": [ex[x] for x in ex if (isinstance(ex[x], float) and "stderr" not in x)][0],
                "fewshots": res.get("config", {}).get("num_fewshot", 0),
            })
    return out

def parse_bslmeval_transformers(paths):
    out = []
    for p in paths:
        res = json.load(open(p, "r"))
        for ex in res.get("results", []):
            out.append({
                "evaluation_framework": "bigscience/lm-evaluation-harness",
                "checkpoint_type": "transformers",
                "task_name": ex.get("task_name", None),
                "prompt_name": ex.get("prompt_name", None),
                "metric": [x for x in ex if (isinstance(ex[x], float) and "stderr" not in x)][0],
                "score": [ex[x] for x in ex if (isinstance(ex[x], float) and "stderr" not in x)][0],
                "fewshots": res.get("config", {}).get("num_fewshot", 0),
            })
    return out


def parse_lmeval_megds(paths):
    out = []
    for p in paths:
        res = json.load(open(p, "r"))
        for k in res.get("results", []):
            for metric, score in res["results"].get(k, {}).items():
                if metric != "acc": continue
                out.append({
                    "evaluation_framework": "EleutherAI/lm-evaluation-harness",
                    "checkpoint_type": "megatrondeepspeed",
                    "task_name": k,
                    "prompt_name": None,
                    "metric": metric,
                    "score": score,
                    "fewshots": 0,
                })
    return out

def parse_codeeval(paths):
    out = []
    for p in paths:
        temp = p.split("_")[-1].replace(".json", "").replace("temp", "")
        for k, v in json.load(open(p, "r")).items():
            out.append({
                "evaluation_framework": "bloom-code-evaluation",
                "checkpoint_type": "transformers",
                "task_name": "openai_humaneval",
                "prompt_name": None,
                "metric": f"{k}-temperature{temp}",
                "score": v,
                "fewshots": 0,
            })
    return out

def parse_bloomzeval(paths):
    out = []
    for p in paths:
        res = json.load(open(p, "r"))
        # NOTE: bigscience/lmevalharness files in bloomzeval folder get skipped
        for metric, score in res.get("evaluation", {}).items():
            task_name = res.get('dataset_name')
            if task_name and res.get('dataset_config_name'):
                task_name = f"{res['dataset_name']}_{res['dataset_config_name']}"
            out.append({
                "evaluation_framework": "bigscience/bloomz",
                "checkpoint_type": "transformers",
                "task_name": task_name,
                "prompt_name": res.get("template_name", None),
                "metric": metric,
                "score": score,
                "fewshots": 0,
            })
    return out


Overwriting evaluation-results/evaluation-results.py


In [17]:
set(bloomz["test"]["evaluation_framework"])

{'bigscience/bloomz',
 'bigscience/lm-evaluation-harness',
 'bloom-code-evaluation'}

In [18]:
bloomz["test"].filter(lambda x: x["task_name"].startswith("wmt"), load_from_cache_file=False)

  0%|          | 0/1 [00:00<?, ?ba/s]

Dataset({
    features: ['evaluation_framework', 'checkpoint_type', 'task_name', 'prompt_name', 'metric', 'score', 'fewshots'],
    num_rows: 20
})

In [27]:
from datasets import load_dataset

mt0_small = load_dataset("evaluation-results", "mt0-small")
mt0_base = load_dataset("evaluation-results", "mt0-base")
mt0_large = load_dataset("evaluation-results", "mt0-large")
mt0_xl = load_dataset("evaluation-results", "mt0-xl")
mt0_xxl = load_dataset("evaluation-results", "mt0-xxl")
mt0_xxl_p3 = load_dataset("evaluation-results", "mt0-xxl-p3")
mt0_xxl_mt = load_dataset("evaluation-results", "mt0-xxl-mt")


bloomz = load_dataset("evaluation-results", "bloomz")
bloomz_7b1 = load_dataset("evaluation-results", "bloomz-7b1")
bloomz_3b = load_dataset("evaluation-results", "bloomz-3b")
bloomz_1b7 = load_dataset("evaluation-results", "bloomz-1b7")
bloomz_1b1 = load_dataset("evaluation-results", "bloomz-1b1")
bloomz_560m = load_dataset("evaluation-results", "bloomz-560m")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating test split: 0 examples [00:00, ? examples/s]

Dataset evaluation-results downloaded and prepared to /root/.cache/huggingface/datasets/evaluation-results/mt0-small/1.0.0/a3f23ee927dcd87543fa60d1adf3c11236ccf38c748219f3ca4dbd57ccb21fee. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating test split: 0 examples [00:00, ? examples/s]

Dataset evaluation-results downloaded and prepared to /root/.cache/huggingface/datasets/evaluation-results/bloomz-560m/1.0.0/a3f23ee927dcd87543fa60d1adf3c11236ccf38c748219f3ca4dbd57ccb21fee. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [28]:
DS = """amazon_reviews_multi_en
amazon_reviews_multi_es
amazon_reviews_multi_fr
amazon_reviews_multi_zh
aqua_rat_raw
art_None
banking77_None
blbooksgenre_title_genre_classifiction
blimp_adjunct_island
climate_fever_None
codah_codah
commonsense_qa_None
conv_ai_3_None
craigslist_bargains_None
emotion_None
financial_phrasebank_sentences
glue_cola
glue_sst2
head_qa_en
head_qa_es
health_fact_None
hlgd_None
hyperpartisan_news_detection_byarticle
liar_None
lince_sa
math_qa_None
mlsum_es
movie_rationales_None
mwsc_None
onestop_english_None
poem_sentiment_None
pubmed_qa_pqa
riddle_sense_None
scicite_None
selqa_answer
snips_built_in_intents_None
wmt14_fr_en_en-fr
wmt14_fr_en_fr-en
wmt14_hi_en_en-hi""".splitlines()
# financial_phrasebank_sentences_allagree -> financial_phrasebank_sentences
# lince_sa_spaeng -> lince_sa
# pubmed_qa_pqa_labeled -> pubmed_qa_pqa
# selqa_answer_selection_analysis -> selqa_answer

DS = ["_".join(d.split("_")[:-1]) for d in DS]


In [32]:
# Inspired by Appendix H from GPT-3
import numpy as np

DS_TO_NAME = {k: k for k in DS}

DS_TO_SPLIT = {
    "super_glue": "validation",
    "xnli": "validation",
    "story_cloze": "validation",
    "Muennighoff/xstory_cloze": "validation",
    "xcopa": "validation",
    "winogrande": "validation",
    "Muennighoff/xwinograd": "test",
    "climate_fever": "test",
    "codah": "train",
    "banking77": "test",
    "blbooksgenre": "train",
    "blimp": "train",
    "emotion": "test",
    "financial_phrasebank": "train",
    "hyperpartisan_news_detection": "train",
    "math_qa": "test",
    "onestop_english": "trsin",
    "pubmed_qa": "train",
    "snips_built_in_intents": "train",

}

MT0_MODEL_TO_RES = {
    "mT0-300M": mt0_small,
    "mT0-560M": mt0_base,
    "mT0-1.2B": mt0_large,
    "mT0-3.7B": mt0_xl,
    "mT0-13B": mt0_xxl,
#    "mT0-13B-MT": mt0_xxl_mt,
#    "mT0-13B-P3": mt0_xxl_p3,    
}

BLOOMZ_MODEL_TO_RES = {
    "BLOOMZ-560M": bloomz_560m,
    "BLOOMZ-1.1B": bloomz_1b1,
    "BLOOMZ-1.7B": bloomz_1b7,
    "BLOOMZ-3B": bloomz_3b,
    "BLOOMZ-7.1B": bloomz_7b1,
#    "BLOOMZ-7.1B-MT": bloomz_7b1_mt,
#    "BLOOMZ-7.1B-P3": bloomz_7b1_p3,
    "BLOOMZ": bloomz,
#    "BLOOMZ-MT": bloomz_mt,
#    "BLOOMZ-P3": bloomz_p3,
}

def get_task(task_name):
    if "wino" in task_name: return "Coref. resolution"
    elif ("story" in task_name) or ("copa" in task_name): return "Sent. completion"
    elif "amazon" in task_name: return "Sentiment"
    elif "art" in task_name: return "Text Classification"
    elif "aqua" in task_name: return "Multiple-Choice QA"
    elif "banking77" in task_name: return "Topic Classification"
    elif "blbooksgenre" in task_name: return "Topic Classification"
    elif "blimp" in task_name: return "Grammar Correction"
    elif "climate" in task_name: return "Text Classification"
    elif "codah" in task_name: return "Multiple-Choice QA"
    elif "commonsense_qa" in task_name: return "Multiple-Choice QA"
    elif "conv_ai_3" in task_name: return "Text Classification"
    elif "craigslist_bargains" in task_name: return "Extractive QA"
    elif "emotion" in task_name: return "Text Classification"
    elif "financial_phrasebank" in task_name: return "Sentiment"
    elif "glue_cola" in task_name: return  "Grammar Correction"
    elif "sst2" in task_name: return  "Sentiment"
    elif "head_qa" in task_name: return  "Multiple-Choice QA"
    elif "health_fact" in task_name: return "Text Classification"
    elif "hlgd" in task_name: return "Text Classification"
    elif "hyperpartisan_news_detection" in task_name: return "Text Classification"
    elif "liar" in task_name: return "Text Classification"
    elif "lince" in task_name: return "Sentiment"
    elif "math_qa" in task_name: return "Multiple-Choice QA"
    elif "mlsum" in task_name: return "Summarization"
    elif "movie_rationales" in task_name: return "Sentiment"
    elif "mwsc" in task_name: return "Multiple-Choice QA"
    elif "onestop_english" in task_name: return "Text Classification"
    elif "poem_sentiment" in task_name: return "Sentiment"
    elif "pubmed_qa" in task_name: return "Multiple-Choice QA"
    elif "riddle_sense" in task_name: return "Multiple-Choice QA"
    elif "scicite" in task_name: return "Text Classification"
    elif "selqa" in task_name: return "Topic Classification"
    elif "snips" in task_name: return "Topic Classification"
    elif "wmt" in task_name: return "Translation"    
    return "NLI"

#HEADER = "\multicolumn{6}{c|}{} & \multicolumn{11}{c}{Pretrained + Multitask finetuned} \\\\"
HEADER = "Task & Dataset & Config & Split & Prompt & Metric"

HEADER += " & " + " & ".join(list(MT0_MODEL_TO_RES.keys()))
HEADER += " & " + " & ".join(list(BLOOMZ_MODEL_TO_RES.keys()))
HEADER += " \\\\"

HEADER += "\n\\midrule\n\\midrule"

TABLE = HEADER

RES_DICT = {}

RES_MAP = {**MT0_MODEL_TO_RES, **BLOOMZ_MODEL_TO_RES}

for ds, ds_name in DS_TO_NAME.items():
    print(f"Running dataset {ds}")
    for name, res_data in RES_MAP.items():
        print(f"Running model {name}")
        # (x["evaluation_framework"]  == "bigscience/bloomz") and 
        ds_data = res_data["test"].filter(lambda x: (x["task_name"].startswith(ds)), load_from_cache_file=False)
        if len(ds_data) == 0:
            print(f"Got no data for {ds}")
        # Iterate through subdatasets
        for task_name in set(ds_data["task_name"]):
            task_ds = ds_data.filter(lambda x: x["task_name"] == task_name)
            config = task_name.split("_")[-1]
            task = get_task(task_name)
            split = DS_TO_SPLIT.get(ds, "validation")

            #print(res_data)
            #print(f"Unexpected len {set(task_ds['prompt_name'])} for {ds} for {task_name} for {name}.")

            prompt_ds_ht = task_ds.filter(lambda x: x["prompt_name"].endswith("ht"))
            prompt_ds_mt = task_ds.filter(lambda x: x["prompt_name"].endswith("mt"))
            prompt_ds_en = task_ds.filter(lambda x: not(x["prompt_name"].endswith(("ht", "mt"))))

            for prompt_ds, prompt in [(prompt_ds_en, "EN"), (prompt_ds_ht, "HT"), (prompt_ds_mt, "MT")]:
                if len(prompt_ds) == 0: continue
                elif len(prompt_ds) != 5: print(f"Unexpected len {len(prompt_ds)} for {ds} for {task_name} for {prompt} for {name}.")
                score_median = np.median([x["score"] for x in prompt_ds])
                score_max = np.max([x["score"] for x in prompt_ds])

                # Undo the *100 lateron as it's already on the right scale
                if ds.startswith(("wmt", "mlsum")):
                    score_median = score_median / 100
                    score_max = score_max / 100

                RES_DICT.setdefault(task, {})
                RES_DICT[task].setdefault(ds, {})
                RES_DICT[task][ds].setdefault(config, {})
                RES_DICT[task][ds][config].setdefault(split, {})
                RES_DICT[task][ds][config][split].setdefault(prompt, {})
                RES_DICT[task][ds][config][split][prompt].setdefault("Median acc.", {})
                RES_DICT[task][ds][config][split][prompt].setdefault("Max acc.", {})
                RES_DICT[task][ds][config][split][prompt]["Median acc."][name] = format(score_median * 100, '.2f')
                RES_DICT[task][ds][config][split][prompt]["Max acc."][name] = format(score_max * 100, '.2f')


for task, vals in sorted(RES_DICT.items()):
    for ds, sub_vals in sorted(vals.items(), key=lambda x: x[0].split("/")[-1]):
        for config, sub_sub_vals in sorted(sub_vals.items()):
            for split, sub_sub_sub_vals in sorted(sub_sub_vals.items()):
                for prompt, sub_sub_sub_sub_vals in sorted(sub_sub_sub_vals.items()):
                    reverse = True if "Max acc." in sub_sub_sub_sub_vals else False # Median first then Max
                    for metric, sub_sub_sub_sub_sub_vals in sorted(sub_sub_sub_sub_vals.items(), reverse=reverse):
                        ONE_LINE = f"{task} & {ds} & {config} & {split} & {prompt} & {metric}" 
                        for name in MT0_MODEL_TO_RES:
                            ONE_LINE += " & " + sub_sub_sub_sub_sub_vals.get(name, "-") 
                        for name in BLOOMZ_MODEL_TO_RES:
                            ONE_LINE += " & " + sub_sub_sub_sub_sub_vals.get(name, "-")                           
                        TABLE += "\n" + ONE_LINE + "\\\\"
    TABLE += "\n\\midrule"

# Escape _ in Latex
TABLE = TABLE.replace("_", "\_")
TABLE = TABLE.replace("Muennighoff/", "")


Running dataset amazon_reviews_multi
Running model mT0-300M


  0%|          | 0/1 [00:00<?, ?ba/s]

Unexpected len 3 for amazon_reviews_multi for amazon_reviews_multi_es for EN for mT0-300M.
Unexpected len 3 for amazon_reviews_multi for amazon_reviews_multi_fr for EN for mT0-300M.


Unexpected len 3 for amazon_reviews_multi for amazon_reviews_multi_en for EN for mT0-300M.
Unexpected len 3 for amazon_reviews_multi for amazon_reviews_multi_zh for EN for mT0-300M.
Running model mT0-560M


  0%|          | 0/1 [00:00<?, ?ba/s]

...

Unexpected len 10 for wmt14_hi_en for wmt14_hi_en for EN for BLOOMZ-3B.
Running model BLOOMZ-7.1B


  0%|          | 0/1 [00:00<?, ?ba/s]

Unexpected len 10 for wmt14_hi_en for wmt14_hi_en for EN for BLOOMZ-7.1B.
Running model BLOOMZ


  0%|          | 0/1 [00:00<?, ?ba/s]

Unexpected len 10 for wmt14_hi_en for wmt14_hi_en for EN for BLOOMZ.


In [33]:
print(TABLE)

Task & Dataset & Config & Split & Prompt & Metric & mT0-300M & mT0-560M & mT0-1.2B & mT0-3.7B & mT0-13B & BLOOMZ-560M & BLOOMZ-1.1B & BLOOMZ-1.7B & BLOOMZ-3B & BLOOMZ-7.1B & BLOOMZ \\
\midrule
\midrule
Extractive QA & craigslist\_bargains & bargains & validation & EN & Median acc. & 30.49 & 23.95 & 22.61 & 39.61 & 25.96 & 38.94 & 47.99 & 28.14 & 22.86 & 46.48 & 26.47\\
Extractive QA & craigslist\_bargains & bargains & validation & EN & Max acc. & 49.41 & 28.14 & 31.32 & 50.92 & 40.54 & 72.53 & 72.36 & 46.90 & 31.32 & 60.47 & 51.76\\
\midrule
Grammar Correction & blimp\_adjunct & island & validation & EN & Median acc. & 50.40 & 51.60 & 51.80 & 53.80 & 55.10 & 51.60 & 52.30 & 50.60 & 49.20 & 49.90 & 49.80\\
Grammar Correction & blimp\_adjunct & island & validation & EN & Max acc. & 50.90 & 57.00 & 58.00 & 59.10 & 56.80 & 77.10 & 60.90 & 62.30 & 59.90 & 57.60 & 51.60\\
Grammar Correction & glue & cola & validation & EN & Median acc. & 30.97 & 38.26 & 56.57 & 35.19 & 45.83 & 31.26 & 57.81 